In [1]:
import requests
import pandas as pd

#Gets a list of all commander-legal sets 
def getsets():
    url = "https://api.scryfall.com/sets"
    response = requests.get(url)
    correcttypes = ["expansion", "commander", "draft_innovation", "core", "from_the_vault", "masters","duel_deck","planechase","starter","box"]
    if response.status_code == 200:
        data = response.json()
        sets = [set_data["code"] for set_data in data["data"] if set_data["set_type"] in correcttypes]
        return sets
    else:
        print("failed")
        return
#Pulls a list of sets and reverses the order (so oldest sets come first in the list )
setlist = getsets()
setlist.reverse()
print(setlist)

['lea', 'leb', '2ed', 'arn', 'atq', '3ed', 'fbb', 'leg', 'sum', 'drk', 'fem', '4ed', '4bb', 'ice', 'bchr', 'chr', 'ren', 'rin', 'hml', 'all', 'rqs', 'mir', 'mgb', 'itp', 'vis', '5ed', 'past', 'por', 'wth', 'tmp', 'sth', 'exo', 'p02', 'usg', 'ath', 'ulg', '6ed', 'ptk', 'uds', 's99', 'mmq', 'brb', 'nem', 's00', 'pcy', 'btd', 'inv', 'pls', '7ed', 'apc', 'psdg', 'ody', 'dkm', 'tor', 'jud', 'ons', 'lgn', 'scg', '8ed', 'mrd', 'dst', '5dn', 'chk', 'bok', 'sok', '9ed', 'psal', 'rav', 'phuk', 'gpt', 'dis', 'csp', 'cst', 'tsb', 'tsp', 'plc', 'fut', '10e', 'me1', 'lrw', 'dd1', 'mor', 'shm', 'eve', 'drb', 'me2', 'ala', 'dd2', 'con', 'ddc', 'arb', 'm10', 'v09', 'hop', 'ohop', 'me3', 'zen', 'ddd', 'wwk', 'dde', 'roe', 'dpa', 'm11', 'v10', 'ddf', 'som', 'td0', 'ps11', 'me4', 'mbs', 'ddg', 'nph', 'td2', 'cmd', 'm12', 'v11', 'ddh', 'isd', 'dka', 'ddi', 'avr', 'pc2', 'opc2', 'm13', 'v12', 'ddj', 'rtr', 'gtc', 'ddk', 'dgm', 'mma', 'm14', 'v13', 'ddl', 'ths', 'c13', 'bng', 'ddm', 'jou', 'md1', 'cns', 'vma

In [25]:
#Gets a list of cards and their related information
#This uses the previous functions to do this
def getcards(setcode):
    url = f"https://api.scryfall.com/cards/search?q=set%3A{setcode}+legal%3Acommander"
    response = requests.get(url)
    if response.status_code == 200:
        data = response.json()
        if 'data' in data:
            card_info = []
            for card in data['data']:
                name = card['name']
                oracle_text = card.get('oracle_text', 'None')
                cmc = card.get("cmc", "None")
                type = card.get("type_line","None")
                mana = card.get("mana_cost","None")
                # reprint = card.get("reprint", "None")
                # cardinfo[name] = [oracle_text, cmc, type, reprint]
                card_info.append((name, oracle_text, cmc, type, mana)) #, cmc, type, keys, reprint
            return card_info
        else:
            print(f"No data found for set {setcode}.")
            return []
    else:
        print(f"Failed to fetch data for set {setcode}. Status code: {response.status_code}")
        return []

    
#Runs the getcards function with each set code that was gathered previously
cardinfolist = list()
for setcode in setlist:
    info = getcards(setcode)
    for i in info: 
        cardinfolist.append(i)
    print(setcode, "complete")

lea complete
leb complete
2ed complete
arn complete
atq complete
3ed complete
fbb complete
leg complete
sum complete
drk complete
fem complete
4ed complete
4bb complete
ice complete
bchr complete
chr complete
ren complete
rin complete
hml complete
all complete
rqs complete
mir complete
mgb complete
itp complete
vis complete
5ed complete
Failed to fetch data for set past. Status code: 404
past complete
por complete
wth complete
tmp complete
sth complete
exo complete
p02 complete
usg complete
ath complete
ulg complete
6ed complete
ptk complete
uds complete
s99 complete
mmq complete
brb complete
nem complete
s00 complete
pcy complete
btd complete
inv complete
pls complete
7ed complete
apc complete
psdg complete
ody complete
dkm complete
tor complete
jud complete
ons complete
lgn complete
scg complete
8ed complete
mrd complete
dst complete
5dn complete
chk complete
bok complete
sok complete
9ed complete
psal complete
rav complete
phuk complete
gpt complete
dis complete
csp complete
cst com

In [28]:
cardinfolist

[('Air Elemental', 'Flying', 5.0, 'Creature — Elemental', '{3}{U}{U}'),
 ('Animate Artifact',
  "Enchant artifact\nAs long as enchanted artifact isn't a creature, it's an artifact creature with power and toughness each equal to its mana value.",
  4.0,
  'Enchantment — Aura',
  '{3}{U}'),
 ('Animate Dead',
  'Enchant creature card in a graveyard\nWhen Animate Dead enters the battlefield, if it\'s on the battlefield, it loses "enchant creature card in a graveyard" and gains "enchant creature put onto the battlefield with Animate Dead." Return enchanted creature card to the battlefield under your control and attach Animate Dead to it. When Animate Dead leaves the battlefield, that creature\'s controller sacrifices it.\nEnchanted creature gets -1/-0.',
  2.0,
  'Enchantment — Aura',
  '{1}{B}'),
 ('Animate Wall',
  "Enchant Wall\nEnchanted Wall can attack as though it didn't have defender.",
  1.0,
  'Enchantment — Aura',
  '{W}'),
 ('Ankh of Mishra',
  "Whenever a land enters the battlef

In [33]:
#Parses our list of all cards into reasonable cards 
name,text,cmc,ctype,mv = [],[],[],[],[]
for i in cardinfolist:
    name.append(i[0])
    text.append(i[1])
    cmc.append(i[2])
    ctype.append(i[3])
    mv.append(i[4])

#Builds the final database based on the card info which was pulled prior
ldf = pd.DataFrame()
ldf["cardname"] = name
ldf["text"] = text
ldf["cmc"] = cmc
ldf["mana"] = mv
ldf["type"] = ctype
ldf.drop_duplicates(keep = "first", inplace = True)
ldf

cardname                                               text  \
0            Air Elemental                                             Flying   
1         Animate Artifact  Enchant artifact\nAs long as enchanted artifac...   
2             Animate Dead  Enchant creature card in a graveyard\nWhen Ani...   
3             Animate Wall  Enchant Wall\nEnchanted Wall can attack as tho...   
4           Ankh of Mishra  Whenever a land enters the battlefield, Ankh o...   
...                    ...                                                ...   
38416      Windswept Heath  {T}, Pay 1 life, Sacrifice Windswept Heath: Se...   
38418     Wooded Foothills  {T}, Pay 1 life, Sacrifice Wooded Foothills: S...   
38458       Legion Loyalty  Creatures you control have myriad. (Whenever a...   
38469  Skyclave Apparition  When Skyclave Apparition enters the battlefiel...   
38481     Whirler Virtuoso  When Whirler Virtuoso enters the battlefield, ...   

       cmc       mana                           type  
0      5.0  {3}{U}{U}           Creature — Elemental  
1      4.0     {3}{U}             Enchantment — Aura  
2      2.0     {1}{B}             Enchantment — Aura  
3      1.0        {W}             Enchantment — Aura  
4      2.0        {2}                       Artifact  
...    ...        ...                            ...  
38416  0.0                                      Land  
38418  0.0                                      Land  
38458  8.0  {6}{W}{W}                    Enchantment  
38469  3.0  {1}{W}{W}          Creature — Kor Spirit  
38481  3.0  {1}{U}{R}  Creature — Vedalken Artificer  

[20400 rows x 5 columns]

In [34]:
#Saves the cardlist to a csv
ldf.to_csv("cardlist.csv")

[('Air Elemental', 'Flying', 5.0, 'Creature — Elemental', '{3}{U}{U}'), ('Animate Artifact', "Enchant artifact\nAs long as enchanted artifact isn't a creature, it's an artifact creature with power and toughness each equal to its mana value.", 4.0, 'Enchantment — Aura', '{3}{U}'), ('Animate Dead', 'Enchant creature card in a graveyard\nWhen Animate Dead enters the battlefield, if it\'s on the battlefield, it loses "enchant creature card in a graveyard" and gains "enchant creature put onto the battlefield with Animate Dead." Return enchanted creature card to the battlefield under your control and attach Animate Dead to it. When Animate Dead leaves the battlefield, that creature\'s controller sacrifices it.\nEnchanted creature gets -1/-0.', 2.0, 'Enchantment — Aura', '{1}{B}'), ('Animate Wall', "Enchant Wall\nEnchanted Wall can attack as though it didn't have defender.", 1.0, 'Enchantment — Aura', '{W}'), ('Ankh of Mishra', "Whenever a land enters the battlefield, Ankh of Mishra deals 2 d